In [1]:
import pandas as pd
import numpy as np
import seaborn as sns

import plotly as py
import plotly.io as pio
import plotly.graph_objs as go
from plotly.subplots import make_subplots

from plotly.offline import init_notebook_mode
# Show charts when running kernel
init_notebook_mode(connected=True)

df = pd.read_csv('spy.us.txt')
df.head()

Date    Open    High     Low   Close    Volume  OpenInt
0  2005-02-25  104.77  106.00  104.68  105.79  70221808        0
1  2005-02-28  105.55  105.68  104.56  105.08  79695344        0
2  2005-03-01  105.22  105.87  105.22  105.62  54607412        0
3  2005-03-02  105.21  106.22  105.10  105.57  73733090        0
4  2005-03-03  105.99  106.20  105.15  105.61  71286823        0


## I. график [OHLC](https://smart-lab.ru/finansoviy-slovar/OHLC)
 __OHLC__ - это столбиковый график **(бары)**, на котором каждый интервал времени **(например 5 минутный)** <br>преставлен OHLC ценами внутри этого временного интервала.
- __O__ — __open__ (цена открытия интервала(бара, японской свечи и т.п.))
- __H__ — __high__ (максимум цены интервала)
- __L__ — __low__  (минимум цены интервала)
- __C__ — __close__(цена закрытия интервала)

In [2]:
fig = go.Figure([go.Ohlc(x=df.Date,
                         open=df.Open,
                         close=df.Close,
                         high=df.High,
                         low=df.Low,)])
# позволяет увеличивать область выделенную прямоугольником
fig.update(layout_xaxis_rangeslider_visible=False)
fig.show()

#  II. [Объем](https://smart-lab.ru/finansoviy-slovar/volume)
__Объем__ - показывает количество акций, торгуемых (купленных, проданных) в течение определенного периода времени, например ежедневно.

Это такой простой, но часто упускаемый из виду индикатор. 
Объем так важен, потому что он в основном представляет собой активность в торговле акциями.
- Более высокое значение объема указывает на более высокие интересы в торговле акциями.

In [3]:
go.Figure(go.Bar(x=df.Date, y=df.Volume, name='Volume', marker_color='red'))

# III. [Moving Averages (MA)](https://smart-lab.ru/finansoviy-slovar/скользящие%20средние)
**Скользящие средние** помогают сглаживать цены акций на графике, отфильтровывая краткосрочные колебания цен.<br> Мы рассчитываем *скользящие средние* за определенный период времени, например, за последние 9, 50 или 200 дней.<br>Есть две (наиболее распространенные) средние, используемые в техническом анализе, которыми являются:

***Simple Moving Average (SMA)*** - простое среднее значение, рассчитанное за последние N дней, например 50, 100 или 200 дней.<br>
***Exponential Moving Average ([EMA](https://smart-lab.ru/blog/22398.php))*** — мувинг смены тенденции.
-  короткий или ***«трендовый»***  период `4 – 7` (short EMA, sEMA)<br>`Идеология`: выступает *поддержкой/сопротивлением* в тренде хвосты(*тени*) баров(*свечей*) должны опираться на него. <br>Рейндж характеризуется нахождением мувинга внутри баров и наличием close баров по обе стороны мувинга.
-  Коррекционный или «***сигнальный***» WMA период `23 – 33` (WMA) <br>`Идеология`: служит уровнем поддержки/сопротивления для коррекционных движений.<br> Пересечение **сигнального** и **трендового** мувинга — формирует предварительный сигнал о возможной смене тренда и предупреждает о попытке **протестировать *Long***.
- Длинный или «***смены тенденции***» EMA период `45 – 65` (long EMA или LEMA)<br>`Идеология`: служит уровнем поддержки/сопротивления для основного тренда.<br> Прежде всего принимается во внимание наклон мувинга и нахождение цены *над* / *под мувингом*, соответственно разделяем «*бычий*» и «*медвежьи*» рынки.<br> - Смена тренда подтверждается изменением наклона мувинга.<br>Как и любая линия поддержки/сопротивления, Long EMA из поддержки превращается в сопротивление и наоборот, в случае его пробоя ценой и смены тренда


In [4]:
df['EMA_9']   = df['Close'].ewm(5).mean().shift()
df['SMA_50']  = df['Close'].rolling(50).mean().shift()
df['SMA_100'] = df['Close'].rolling(100).mean().shift()
df['SMA_200'] = df['Close'].rolling(200).mean().shift()

fig = go.Figure()
fig.add_trace(go.Scatter(x=df.Date, y=df.EMA_9, name='EMA 9'))
fig.add_trace(go.Scatter(x=df.Date, y=df.SMA_50, name='SMA 50'))
fig.add_trace(go.Scatter(x=df.Date, y=df.SMA_100, name='SMA 100'))
fig.add_trace(go.Scatter(x=df.Date, y=df.SMA_200, name='SMA 200'))
fig.add_trace(go.Scatter(x=df.Date, y=df.Close, name='Close', line_color='dimgray', opacity=0.3))
fig.show()



df['EMA_5']  = df['Close'].ewm(5).mean().shift()
df['EMA_25'] = df['Close'].ewm(25).mean().shift()
df['EMA_55'] = df['Close'].ewm(55).mean().shift()
fig = go.Figure()
fig.add_trace(go.Scatter(x=df.Date, y=df.EMA_5, name='sEMA'))
fig.add_trace(go.Scatter(x=df.Date, y=df.EMA_25, name='WMA'))
fig.add_trace(go.Scatter(x=df.Date, y=df.EMA_55, name='Long EMA'))
fig.add_trace(go.Scatter(x=df.Date, y=df.Close, name='Close', line_color='dimgray', opacity=0.3))
fig.show()

# IV. Relative Strength Index [RSI](https://smart-lab.ru/finansoviy-slovar/RSI) 
***«Индекс относительной силы»*** — индикатор, отражающий силу тренда.<br> 
- Расчитывается как сумма всех движений цены вверх, деленная на сумму всех движений цены вниз на выбранном временном интервале.
### Он может показать, что акции либо перекуплены, либо перепроданы. 
- Обычно значение *RSI* `> 70` сигнализирует о том, что акция становится перекупленной/переоцененной
- начение `< 30`  означает, что она перепродана.

In [5]:
def RSI(df, n=14):
    close = df['Close']
    delta = close.diff()[1:]
    pricesUp   = delta.copy()
    pricesDown = delta.copy()
    pricesUp[pricesUp < 0] = 0
    pricesDown[pricesDown > 0] = 0
    rollUp = pricesUp.rolling(n).mean()
    rollDown = pricesDown.abs().rolling(n).mean()
    rs = rollUp / rollDown
    rsi = 100.0 - (100.0 / (1.0 + rs))
    return rsi

num_days = 365
df['RSI'] = RSI(df).fillna(0)
fig = go.Figure(go.Scatter(x=df.Date.tail(num_days), y=df.RSI.tail(num_days)))
fig.show()

# V. Moving Average Convergence Divergence [MACD](https://smart-lab.ru/finansoviy-slovar/MACD)
индикатор, показывающий взаимосвязь между двумя экспоненциальными скользящими средними<br>
***MACD*** = *`12`-Period EMA  − `26`-Period EMA*

***MACD*** может быть использован для анализа ведения торгов на пересечениях основных линий , дивергенции, на уровнях перекупки/перепродажи. Данный инструмент может быть очень полезен для определения тренда рынка.

In [6]:
EMA_12 = pd.Series(df['Close'].ewm(span=12, min_periods=12).mean())
EMA_26 = pd.Series(df['Close'].ewm(span=26, min_periods=26).mean())
MACD = pd.Series(EMA_12 - EMA_26)
MACD_signal = pd.Series(MACD.ewm(span=9, min_periods=9).mean())

fig = make_subplots(rows=2, cols=1)
fig.add_trace(go.Scatter(x=df.Date, y=df.Close, name='Close'), row=1, col=1)
fig.add_trace(go.Scatter(x=df.Date, y=EMA_12, name='EMA 12'),  row=1, col=1)
fig.add_trace(go.Scatter(x=df.Date, y=EMA_26, name='EMA 26'),  row=1, col=1)

fig.add_trace(go.Scatter(x=df.Date, y=MACD, name='MACD'),      row=2, col=1)
fig.add_trace(go.Scatter(x=df.Date, y=MACD_signal, name='Signal line'), row=2, col=1)
fig.show()

# VI. [Stochastic](https://smart-lab.ru/blog/172466.php)
$ K=(\frac{C−L_{14}}{H_{14}−L_{14}})×100$<br>
 **C**- самая последняя цена закрытия<br>
 **L14, H14** - самые низкие / самые высокие цены, торгуемые за последние 14 дней.<br>
 
Этот стохастик ***K*** часто называют "slow stochastic indicator". Существует также "fast stochastic indicator", который можно получить в виде:
$ D=SMA_3(K) $


In [7]:
def stochastic(df, k, d):
    df = df.copy()
    low_min  = df['Low'].rolling(k).min()
    high_max = df['High'].rolling(k).max()
    df['stoch_k'] = 100 * (df['Close'] - low_min)/(high_max - low_min)
    df['stoch_d'] = df['stoch_k'].rolling(d).mean()
    return df

stochs = stochastic(df, k=14, d=3)

fig = go.Figure()
fig.add_trace(go.Scatter(x=df.Date.tail(365), y=stochs.stoch_k.tail(365), name='K stochastic'))
fig.add_trace(go.Scatter(x=df.Date.tail(365), y=stochs.stoch_d.tail(365), name='D stochastic'))
fig.show()